# Finding the Right Dose

David Augustin

In [1]:
#
# Slide 1: Scatter plot of control tumour growth.
#

import os

import pandas as pd
import plotly.graph_objects as go


# Create figure
fig = go.Figure()

# Import data
# Get path of directory one up current working directory
path = os.path.dirname(os.getcwd())

# Import LXF A677 control growth data
lxf_data = pd.read_csv(path + '/notebooks/control_growth/data/lxf_control_growth.csv')

# Scatter plot LXF A677 time-series data for each mouse
mouse_ids = lxf_data['#ID'].unique()
for id_m in mouse_ids:
    # Create mask for mouse
    mask = lxf_data['#ID'] == id_m

    # Get time points for mouse
    times = lxf_data['TIME in day'][mask]

    # Get observed tumour volumes for mouse
    observed_volumes = lxf_data['TUMOUR VOLUME in cm^3'][mask]

    # Plot data
    fig.add_trace(go.Scatter(
        x=times,
        y=observed_volumes,
        name="ID: %s" % id_m,
        showlegend=True,
        hovertemplate=
            "<b>ID: %d</b><br>" % id_m +
            "Cancer type: LXF A677<br>"
            "Time: %{x:} day<br>" +
            "Tumour volume: %{y:.02f} cm^3<br>" +
            "<extra></extra>",
        mode="markers",
        marker=dict(
            symbol='circle',
            opacity=0.7,
            line=dict(color='black', width=1))
    ))

# Set X, Y axis and figure size
fig.update_layout(
    autosize=False,
    width=800,
    height=600,
    xaxis_title=r'$\text{Time in day}$',
    yaxis_title=r'$\text{Tumour volume in cm}^3$',
    template="plotly_white")

# Add switch between linear and log y-scale
fig.update_layout(
    updatemenus=[
        dict(
            type = "buttons",
            direction = "left",
            buttons=list([
                dict(
                    args=[{"yaxis.type": "linear"}],
                    label="Linear y-scale",
                    method="relayout"
                ),
                dict(
                    args=[{"yaxis.type": "log"}],
                    label="Log y-scale",
                    method="relayout"
                )
            ]),
            pad={"r": 0, "t": -10},
            showactive=True,
            x=0.0,
            xanchor="left",
            y=1.15,
            yanchor="top"
        ),
    ]
)

# Show figure
fig.show()

Notes:
- Describe axes
- Colours indicate individuals
- The trend is the same
- BUT there are subsantial differences bewtween the individuals

### There is substantial variation between individuals!

In [ ]:
# TODO: Currently tumour volume transformed to cm^3 by hand!!!
#
# Slide 3: Scatter plot of treated mice.
#

import os

import numpy as np
import pandas as pd
import plotly.colors
import plotly.graph_objects as go
from plotly.subplots import make_subplots

import pkpd.utils


path = os.path.dirname(os.getcwd())

# Import LXF A677 Erlotinib low dose data
low_dose_data = pd.read_csv(
    path + '/notebooks/lung_cancer/erlotinib/treatment_low_dose/data/erlotinib_low_dose_lxf.csv')

# Import LXF A677 Erlotinib intermediate dose data
inter_dose_data = pd.read_csv(
    path + '/notebooks/lung_cancer/erlotinib/treatment_intermediate_dose/data/erlotinib_intermediate_dose_lxf.csv')

# Get number of individual mice
n_mice = len(low_dose_data['#ID'].unique())

# Define colorscheme
colors = plotly.colors.qualitative.Plotly[:n_mice]

# Create figure
fig = make_subplots(rows=2, cols=1, shared_xaxes=True, row_heights=[0.3, 0.7], vertical_spacing=0.05)

# Scatter plot of concentration and tumour growth data
for index, mouse_id in enumerate(np.sort(low_dose_data['#ID'].unique())):
    # Mask dataset for mouse
    mask = low_dose_data['#ID'] == mouse_id
    mouse_data = low_dose_data[mask]

    # Get tumour volume measurement times
    volume_times = mouse_data['TIME VOLUME in day'].to_numpy()

    # Get measured concentrations
    volumes = mouse_data['TUMOUR VOLUME in cm^3'].to_numpy() / 10**3

    # Get dosing time points
    dose_times = mouse_data['TIME DOSE in day'].to_numpy()

    # Get doses
    doses = mouse_data['DOSE AMOUNT in mg'].to_numpy()

    # Filter nans from dose arrays
    dose_times = dose_times[~np.isnan(dose_times)]
    doses = doses[~np.isnan(doses)]

    # Convert dose events to cumulative dose amount time series
    dose_times, doses = pkpd.utils.compute_cumulative_dose_amount(
        times=dose_times,
        doses=doses,
        end_exp=30)

    # Plot cumulative dosed amount
    fig.add_trace(
        go.Scatter(
            x=dose_times,
            y=doses,
            legendgroup="ID: %d" % mouse_id,
            name="ID: %d" % mouse_id,
            showlegend=False,
            hovertemplate=
                "<b>Cumulative dose in mg</b><br>" +
                "ID: %d<br>" % mouse_id +
                "Time: %{x:.0f} day<br>" +
                "Tumour volume: %{y:.02f} cm^3<br>" +
                "<extra></extra>",
            mode="lines",
            line=dict(color=colors[index])),
        row=1,
        col=1)

    # Plot tumour volume data
    fig.add_trace(
        go.Scatter(
            x=volume_times,
            y=volumes,
            legendgroup="ID: %d" % mouse_id,
            name="ID: %d" % mouse_id,
            showlegend=True,
            hovertemplate=
                "<b>Tumour volume in cm^3</b><br>" +
                "ID: %d<br>" % mouse_id +
                "Time: %{x:} day<br>" +
                "Tumour volume: %{y:.02f} cm^3<br>" +
                "<extra></extra>",
            mode="markers",
            marker=dict(
                symbol='circle',
                opacity=0.7,
                line=dict(color='black', width=1),
                color=colors[index])),
        row=2,
        col=1)

# Get number of individual mice
n_mice = len(inter_dose_data['#ID'].unique())

# Define colorscheme
colors = plotly.colors.qualitative.Plotly[:n_mice]

# Scatter plot of concentration and tumour growth data
for index, mouse_id in enumerate(np.sort(inter_dose_data['#ID'].unique())):
    # Mask dataset for mouse
    mask = inter_dose_data['#ID'] == mouse_id
    mouse_data = inter_dose_data[mask]

    # Get tumour volume measurement times
    volume_times = mouse_data['TIME VOLUME in day'].to_numpy()

    # Get measured concentrations
    volumes = mouse_data['TUMOUR VOLUME in cm^3'].to_numpy() / 10**3

    # Get dosing time points
    dose_times = mouse_data['TIME DOSE in day'].to_numpy()

    # Get doses
    doses = mouse_data['DOSE AMOUNT in mg'].to_numpy()

    # Filter nans from dose arrays
    dose_times = dose_times[~np.isnan(dose_times)]
    doses = doses[~np.isnan(doses)]

    # Convert dose events to cumulative dose amount time series
    dose_times, doses = pkpd.utils.compute_cumulative_dose_amount(
        times=dose_times,
        doses=doses,
        end_exp=30)

    # Plot cumulative dosed amount
    fig.add_trace(
        go.Scatter(
            x=dose_times,
            y=doses,
            legendgroup="ID: %d" % mouse_id,
            name="ID: %d" % mouse_id,
            showlegend=False,
            visible=False,
            hovertemplate=
                "<b>Cumulative dose in mg</b><br>" +
                "ID: %d<br>" % mouse_id +
                "Time: %{x:.0f} day<br>" +
                "Tumour volume: %{y:.02f} cm^3<br>" +
                "<extra></extra>",
            mode="lines",
            line=dict(color=colors[index])),
        row=1,
        col=1)

    # Plot tumour volume data
    fig.add_trace(
        go.Scatter(
            x=volume_times,
            y=volumes,
            legendgroup="ID: %d" % mouse_id,
            name="ID: %d" % mouse_id,
            showlegend=True,
            visible=False,
            hovertemplate=
                "<b>Tumour volume in cm^3</b><br>" +
                "ID: %d<br>" % mouse_id +
                "Time: %{x:} day<br>" +
                "Tumour volume: %{y:.02f} cm^3<br>" +
                "<extra></extra>",
            mode="markers",
            marker=dict(
                symbol='circle',
                opacity=0.7,
                line=dict(color='black', width=1),
                color=colors[index])),
        row=2,
        col=1)

# Set figure size
fig.update_layout(
    autosize=False,
    width=800,
    height=600,
    template="plotly_white")

# Set X axis label
fig.update_xaxes(title_text=r'$\text{Time in day}$', row=2, col=1)

# Set Y axes labels
fig.update_yaxes(title_text=r'$\text{Amount in mg}$', row=1, col=1)
fig.update_yaxes(title_text=r'$\text{Tumour volume in cm}^3$', row=2, col=1)

# Add switch between linear and log y-scale
fig.update_layout(
    updatemenus=[
        dict(
            type = "buttons",
            direction = "left",
            buttons=list([
                dict(
                    args=[{"yaxis2.type": "linear"}],
                    label="Linear y-scale",
                    method="relayout"
                ),
                dict(
                    args=[{"yaxis2.type": "log"}],
                    label="Log y-scale",
                    method="relayout"
                )
            ]),
            pad={"r": 0, "t": -10},
            showactive=True,
            x=0.0,
            xanchor="left",
            y=1.15,
            yanchor="top"
        ),
        dict(
            type = "buttons",
            direction = "down",
            buttons=list([
                dict(
                    args=[{"visible": [True]*16 + [False]*16}],
                    label="6.25 mg/kg/day",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*16 + [True]*16}],
                    label="25 mg/kg/day",
                    method="restyle"
                )
            ]),
            pad={"r": 0, "t": -10},
            showactive=True,
            x=1.07,
            xanchor="left",
            y=1.1,
            yanchor="top"
        ),
    ]
)

# Position legend
fig.update_layout(legend=dict(
    yanchor="bottom",
    y=0.01,
    xanchor="left",
    x=1.05))

# Show figure
fig.show()


Notes:
- Different dosing strategies with Erlotinib
- Erlotinib is a drug that is already used in clinical practice to treat a variety of epidemoid cancers.
- Top sub-figure: Total administered amount
- Bottom sub-figure: Tumour volume
- Again the overall trend of the tumour growth is similar
- BUT there are substantial differences in the response between individuals

## There is no standard optimal dose for everybody!

## Naïve approach to find personalised doses

1. Write down a structural model for the tumour growth and the effects of the drug
2. Write down model for deviations of structural model from observations
3. Fit model measurements of individual and predict future behaviour

## Structural model for tumour growth in absence of compound

\begin{equation*}
    \frac{\text{d}V^s_T}{\text{d}t} = \frac{2\lambda _0\lambda _1 V^s_T}{2\lambda _0 V^s_T + \lambda _1}
\end{equation*}

Here, $V^s_T$ is the predicted tumour volume by the structural model, $\lambda _0$ is the exponential growth rate, and $\lambda _1$ is the linear growth rate. The tumour growth of an individual in absence of the drug is thus parameterised by three parameters

\begin{equation*}
    \psi = (V_0, \lambda _0, \lambda _1),
\end{equation*}

where $V_0$ is the initial tumour volume, $V^s_T(t=0, \psi) = V_0$.

## Error model for deviations between structural model and observations

\begin{equation*}
    \varepsilon = \left(\sigma _{\text{base}} + \sigma _{\text{rel}} V^s_T\right) \varepsilon _n
\end{equation*}

Here, $\sigma _{\text{base}}$ is the standard deviation of the base-level noise, and $\sigma _{\text{rel}}$ is the standard deviation relative to $V^s_T$. $\varepsilon _n$ is a standard Gaussian random variable $\mathcal{N}(0, 1)$.

As a result, the model predictions of the tumour volume are Gaussian-distributed, centered at the structural model predictions $V^s_T = V^s_T(t; \psi)$ with a standard deviation $\sigma _{\text{tot}} = \sigma _{\text{base}} + \sigma _{\text{rel}} V^s_T$

\begin{equation*}
    V_T \sim \mathcal{N}(V^s_T, \sigma ^2_{\text{tot}}).
\end{equation*}

The error model introduces two further parameters to the model

\begin{equation*}
    \theta _V = (\sigma _{\text{base}}, \sigma _{\text{rel}}),
\end{equation*}

such that at this point the PKPD model has 5 parameters ($\psi$, $\theta _V$).

In [3]:
#
# Define pints model wrapper such that myokit model can be used for inference.
#

import myokit
import pints

from pkpd import model as model


# Wrap myokit model, so it can be used with pints
class PintsModel(pints.ForwardModel):
    def __init__(self):
        # Create myokit model
        model = m.create_tumour_growth_model()

        # Create simulator
        self.sim = myokit.Simulation(model)

    def n_parameters(self):
        """
        Number of parameters to fit. Here initial V^s_T, lambda_0, lambda_1
        """
        return 3

    def n_outputs(self):
        return 1

    def simulate(self, parameters, times):
        # Reset simulation
        self.sim.reset()

        # Sort input parameters
        initial_volume, lambda_0, lambda_1 = parameters

        # Set initial condition
        self.sim.set_state([initial_volume])

        # Set growth constants
        self.sim.set_constant('central.lambda_0', lambda_0)
        self.sim.set_constant('central.lambda_1', lambda_1)

        # Define logged variable
        loggedVariable = 'central.volume_t'

        # Simulate
        output = self.sim.run(times[-1] + 1, log=[loggedVariable], log_times=times)
        result = output[loggedVariable]

        return np.array(result)

In [4]:
#
# Naive attempt to find an optimal parameter set psi for each mouse in the LXF A677 and VXF A431 population.
#
# This cell needs above defined wrapped myokit model:
# [PintsModel]
#

import os

import numpy as np
import pandas as pd
import pints

import pkpd.model as m


# Import data
# Get path of directory one up current working directory
path = os.path.dirname(os.getcwd())

# Import LXF A677 control growth data
lxf_data = pd.read_csv(path + '/notebooks/control_growth/data/lxf_control_growth.csv')
n_mice_lxf = len(lxf_data['#ID'].unique())

# Define container for the structural model estimates
# Shape (n_mice, n_parameters)
n_parameters = 5  # (model params, eta, sigma)
lxf_mouse_parameters = np.empty(shape=(n_mice_lxf, n_parameters))

# Define arbitrary starting point for the optimisations
initial_parameters = [1, 1, 1, 1, 0.1]

# Find mouse parameters for LXF A677 population
mouse_ids = lxf_data['#ID'].unique()
for index, mouse_id in enumerate(mouse_ids):
    # Create mask for mouse with specfied ID
    mouse_mask = lxf_data['#ID'] == mouse_id

    # Get relevant time points
    times = lxf_data[mouse_mask]['TIME in day'].to_numpy()

    # Get measured tumour volumes
    observed_volumes = lxf_data[mouse_mask]['TUMOUR VOLUME in cm^3'].to_numpy()

    # Create inverse problem
    problem = pints.SingleOutputProblem(PintsModel(), times, observed_volumes)

    # Create likelihood
    likelihood = pints.MultiplicativeGaussianLogLikelihood(problem)

    # Create priors
    prior = pints.UniformLogPrior([0.001, 0.001, 0.001, 0.9, 0.001], [1E3, 1E3, 1E3, 1.1, 1E3])

    # Create posterior
    posterior = pints.LogPosterior(likelihood, prior)

    # Create optimisation controller with a CMA-ES optimiser
    optimiser = pints.OptimisationController(
        function=posterior,
        x0=initial_parameters,
        method=pints.CMAES)

    # Disable logging mode
    optimiser.set_log_to_screen(False)

    # Parallelise optimisation
    optimiser.set_parallel(True)

    # Find optimal parameters
    estimates, _ = optimiser.run()

    # Save estimates
    lxf_mouse_parameters[index, :] = estimates

/Users/david/Documents/SABS/DPhil/Rotation 1 - PKPD Modelling Workflow/notebooks/ErlotinibGefitinib/venv/lib/python3.7/site-packages/cma/evolution_strategy.py:3591: RuntimeWarning:

invalid value encountered in double_scalars



In [5]:
#
# Solve structural model for inferred model parameters.
#
# This cell needs the above defined wrapped myokit model, and the inferred model parameters:
# [PintsModel, lxf_mouse_parameters]
#

import numpy as np


# Create tumour growth model
model = PintsModel()

# Define simulation time points in day
times = np.linspace(start=0, stop=30, num=200)
n_times = len(times)

# Create container for simulated tumour growth
# Shape (n_mice, n_times)
n_mice = len(lxf_mouse_parameters)
lxf_tumour_growth = np.empty(shape=(n_mice, n_times))

# Solve structural model for LXF A677 population
for mouse_id, mouse_params in enumerate(lxf_mouse_parameters):
    # Get relevant parameters
    params = mouse_params[:3]
    
    # Simulate mouse tumour growth
    lxf_tumour_growth[mouse_id, :] = model.simulate(parameters=params, times=times)


In [6]:
#
# Visualise simulated tumour growth together with control growth data.
#
# This cell needs the above simulated tumour growth and the control growth data:
# [times, lxf_tumour_growth, lxf_data]
#

import pandas as pd
import plotly.colors
import plotly.graph_objects as go


# Get number of individual mice
n_mice_lxf = len(lxf_tumour_growth)

# Define colorscheme
colors = plotly.colors.qualitative.Plotly[:n_mice_lxf]

# Create figure
fig = go.Figure()

# Scatter plot LXF A677 time-series data for each mouse
mouse_ids = lxf_data['#ID'].unique()
for index, id_m in enumerate(mouse_ids):
    # Create mask for mouse
    mask = lxf_data['#ID'] == id_m

    # Get time points for mouse
    observed_times = lxf_data['TIME in day'][mask]

    # Get observed tumour volumes for mouse
    observed_volumes = lxf_data['TUMOUR VOLUME in cm^3'][mask]

    # Get simulated tumour volumes for mouse
    simulated_volumes = lxf_tumour_growth[index, :]

    # Plot data
    fig.add_trace(go.Scatter(
        x=observed_times,
        y=observed_volumes,
        legendgroup="ID: %d" % id_m,
        name="ID: %d" % id_m,
        showlegend=True,
        hovertemplate=
            "<b>Measurements %s</b><br>" % ("LXF A677") +
            "ID: %d<br>" % id_m +
            "Time: %{x:} day<br>" +
            "Tumour volume: %{y:.02f} cm^3<br>" +
            "<extra></extra>",
        mode="markers",
        marker=dict(
            symbol='circle',
            opacity=0.7,
            line=dict(color='black', width=1),
            color=colors[index])
    ))

    # Plot simulated growth
    fig.add_trace(go.Scatter(
        x=times,
        y=simulated_volumes,
        legendgroup="ID: %d" % id_m,
        name="ID: %d" % id_m,
        showlegend=False,
        visible=False,
        hovertemplate=
            "<b>Simulation %s</b><br>" % ("LXF A677") +
            "ID: %d<br>" % id_m +
            "Time: %{x:.0f} day<br>" +
            "Tumour volume: %{y:.02f} cm^3<br>" +
            "<extra></extra>",
        mode="lines",
        line=dict(color=colors[index])
    ))

# Set figure size
fig.update_layout(
    autosize=False,
    width=800,
    height=600,
    template="plotly_white")


# Set X axis label
fig.update_xaxes(title_text=r'$\text{Time in day}$')

# Set Y axes labels
fig.update_yaxes(title_text=r'$\text{Tumour volume in cm}^3$')

# Add switch between linear and log y-scale
fig.update_layout(
    updatemenus=[
        dict(
            type = "buttons",
            direction = "left",
            buttons=list([
                dict(
                    args=[{"yaxis.type": "linear"}],
                    label="Linear y-scale",
                    method="relayout"
                ),
                dict(
                    args=[{"yaxis.type": "log"}],
                    label="Log y-scale",
                    method="relayout"
                )
            ]),
            pad={"r": 0, "t": -10},
            showactive=True,
            x=0.0,
            xanchor="left",
            y=1.15,
            yanchor="top"
        ),
        dict(
            type = "buttons",
            direction = "down",
            buttons=list([
                dict(
                    args=[{"visible": [True, False]*8}],
                    label="Data",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [True]*16}],
                    label="Data + Fits",
                    method="restyle"
                )
            ]),
            pad={"r": 0, "t": -10},
            showactive=True,
            x=1.07,
            xanchor="left",
            y=1.1,
            yanchor="top"
        ),
    ]
)

# Position legend
fig.update_layout(legend=dict(
    yanchor="bottom",
    y=0.01,
    xanchor="left",
    x=1.05))

# Show figure
fig.show()

## Model captures observed behaviour, but how predictable is this approach?

In [7]:
#
# Illustrate convergence of indiviually fitted parameters.
#
# This cell needs above defined wrapped myokit model:
# [PintsModel]
#

import os

import numpy as np
import pandas as pd
import pints

import pkpd.model as m


# Import data
# Get path of directory one up current working directory
path = os.path.dirname(os.getcwd())

# Import LXF A677 control growth data
lxf_data = pd.read_csv(path + '/notebooks/control_growth/data/lxf_control_growth.csv')

# Get a mouse 
mice_ids = lxf_data['#ID'].unique()
mask = lxf_data['#ID'] == mice_ids[0]
mouse_data = lxf_data[mask]

# Get relevant time points
all_times = mouse_data['TIME in day'].to_numpy()
n_times = len(all_times)

# Get measured tumour volumes
all_observed_volumes = mouse_data['TUMOUR VOLUME in cm^3'].to_numpy()

# Define container for the structural model estimates when
# for each inference data is used up to a specfied time point
# Shape (n_data_points, n_parameters)
n_parameters = 5
mouse_parameters = np.empty(shape=(n_times, n_parameters))

# Define arbitrary starting point for the optimisations
initial_parameters = [1, 1, 1, 1, 0.1]

# Find mouse parameters for mice by iteratively appending measurements
for data_id in range(n_times):
    # Get relevant time points
    times = all_times[:data_id+1]

    # Get measured tumour volumes
    observed_volumes = all_observed_volumes[:data_id+1]

    # Create inverse problem
    problem = pints.SingleOutputProblem(PintsModel(), times, observed_volumes)

    # Create likelihood
    likelihood = pints.MultiplicativeGaussianLogLikelihood(problem)

    # Create priors
    prior = pints.UniformLogPrior([0.001, 0.001, 0.001, 0.9, 0.001], [1E3, 1E3, 1E3, 1.1, 1E3])

    # Create posterior
    posterior = pints.LogPosterior(likelihood, prior)

    # Create optimisation controller with a CMA-ES optimiser
    optimiser = pints.OptimisationController(
        function=posterior,
        x0=initial_parameters,
        method=pints.CMAES)

    # Disable logging mode
    optimiser.set_log_to_screen(False)

    # Parallelise optimisation
    optimiser.set_parallel(True)

    # Find optimal parameters
    estimates, _ = optimiser.run()

    # Save estimates
    mouse_parameters[data_id, :] = estimates

In [8]:
#
# Solve structural model for inferred model parameters.
#
# This cell needs the above defined wrapped myokit model, and the inferred model parameters:
# [PintsModel, mouse_parameters]
#

import numpy as np


# Create tumour growth model
model = PintsModel()

# Define simulation time points in day
times = np.linspace(start=0, stop=30)
n_times_sim = len(times)

# Create container for simulated tumour growth
# Shape (n_times_data, n_times_sim)
n_times_data = len(mouse_parameters)
simulated_tumour_growth = np.empty(shape=(n_times_data, n_times_sim))

# Solve structural model for LXF A677 population
for params_id, mouse_params in enumerate(mouse_parameters):
    # Get relevant parameters [intial volume, lamda_0, lambda_1]
    params = mouse_params[:3]
    
    # Simulate mouse tumour growth
    simulated_tumour_growth[params_id, :] = model.simulate(parameters=params, times=times)


In [9]:
#
# Visualise simulated tumour growth together with control growth data.
#
# This cell needs the above simulated tumour growth and the control growth data:
# [times, simulated_tumour_growth, mouse_data]
#

import pandas as pd
import plotly.colors
import plotly.graph_objects as go


# Get number of optimisations
n_opt = len(simulated_tumour_growth)

# Define colorscheme
color = plotly.colors.qualitative.Plotly[0]

# Create figure
fig = go.Figure()

# Get Mouse id
mouse_id = mouse_data['#ID'][0]

# Get relevant time points
all_times = mouse_data['TIME in day'].to_numpy()
n_times = len(all_times)

# Get measured tumour volumes
all_observed_volumes = mouse_data['TUMOUR VOLUME in cm^3'].to_numpy()

# Scatter plot mouse data up to specified time
for data_id in range(n_times):
    # Get training data times
    observed_times_train = all_times[:data_id+1]

    # Get remaining data times
    observed_times = all_times[data_id+1:]

    # Get training data volumes
    observed_volumes_train = all_observed_volumes[:data_id+1]

    # remaining data volumes
    observed_volumes = all_observed_volumes[data_id+1:]

    # Get simulated tumour volumes for mouse
    simulated_volumes = simulated_tumour_growth[data_id, :]

    # Plot data train data
    fig.add_trace(go.Scatter(
        x=observed_times_train,
        y=observed_volumes_train,
        legendgroup="ID: %d" % mouse_id,
        name="ID: %d" % mouse_id,
        showlegend=True,
        visible=True if data_id == 0 else False,
        hovertemplate=
            "<b>Measurements %s</b><br>" % ("LXF A677") +
            "ID: %d<br>" % mouse_id +
            "Time: %{x:} day<br>" +
            "Tumour volume: %{y:.02f} cm^3<br>" +
            "<extra></extra>",
        mode="markers",
        marker=dict(
            symbol='circle',
            opacity=0.7,
            line=dict(color='black', width=1),
            color=color)
    ))

    # Plot data remaining data
    fig.add_trace(go.Scatter(
        x=observed_times,
        y=observed_volumes,
        legendgroup="ID: %d" % mouse_id,
        name="ID: %d" % mouse_id,
        showlegend=False,
        visible=True if data_id == 0 else False,
        hovertemplate=
            "<b>Measurements %s</b><br>" % ("LXF A677") +
            "ID: %d<br>" % mouse_id +
            "Time: %{x:} day<br>" +
            "Tumour volume: %{y:.02f} cm^3<br>" +
            "<extra></extra>",
        mode="markers",
        marker=dict(
            symbol='circle',
            opacity=0.2,
            line=dict(color='black', width=1),
            color=color)
    ))

    # Plot simulated growth
    fig.add_trace(go.Scatter(
        x=times,
        y=simulated_volumes,
        legendgroup="ID: %d" % mouse_id,
        name="ID: %d" % mouse_id,
        showlegend=False,
        visible=True if data_id == 0 else False,
        hovertemplate=
            "<b>Simulation %s</b><br>" % ("LXF A677") +
            "ID: %d<br>" % mouse_id +
            "Time: %{x:.0f} day<br>" +
            "Tumour volume: %{y:.02f} cm^3<br>" +
            "<extra></extra>",
        mode="lines",
        line=dict(color=color)
    ))

# Set figure size
fig.update_layout(
    autosize=False,
    width=800,
    height=600,
    template="plotly_white")


# Set X axis label
fig.update_xaxes(title_text=r'$\text{Time in day}$')

# Set Y axes labels
fig.update_yaxes(title_text=r'$\text{Tumour volume in cm}^3$')

# Add switch between linear and log y-scale
fig.update_layout(
    updatemenus=[
        dict(
            type = "buttons",
            direction = "left",
            buttons=list([
                dict(
                    args=[{"yaxis.type": "linear"}],
                    label="Linear y-scale",
                    method="relayout"
                ),
                dict(
                    args=[{"yaxis.type": "log"}],
                    label="Log y-scale",
                    method="relayout"
                )
            ]),
            pad={"r": 0, "t": -10},
            showactive=True,
            x=0.0,
            xanchor="left",
            y=1.15,
            yanchor="top"
        ),
        dict(
            type = "buttons",
            direction = "down",
            buttons=list([
                dict(
                    args=[{"visible": [True]*3 + [False]*(3 * (n_times - 1))}],
                    label="1 data point",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*3 + [True]*3 + [False]*(3 * (n_times - 2))}],
                    label="2 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 2) + [True]*3 + [False]*(3 * (n_times - 3))}],
                    label="3 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 3) + [True]*3 + [False]*(3 * (n_times - 4))}],
                    label="4 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 4) + [True]*3 + [False]*(3 * (n_times - 5))}],
                    label="5 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 5) + [True]*3 + [False]*(3 * (n_times - 6))}],
                    label="6 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 6) + [True]*3 + [False]*(3 * (n_times - 7))}],
                    label="7 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 7) + [True]*3 + [False]*(3 * (n_times - 8))}],
                    label="8 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 8) + [True]*3 + [False]*(3 * (n_times - 9))}],
                    label="9 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 9) + [True]*3 + [False]*(3 * (n_times - 10))}],
                    label="10 data points",
                    method="restyle"
                )
            ]),
            pad={"r": 0, "t": -10},
            showactive=True,
            x=1.07,
            xanchor="left",
            y=1.1,
            yanchor="top"
        ),
    ]
)

# Position legend
fig.update_layout(legend=dict(
    yanchor="bottom",
    y=0.01,
    xanchor="left",
    x=1.05))

# Show figure
fig.show()

## Let's leverage the biological similarities between individuals

## Population PKPD model approach to find personalised doses

1. Write down a structural model for the tumour growth and the effects of the drug
2. Write down model for deviations of structural model from observations
3. Write down model for variation in population
4. Fit model to population behaviour
5. Use population information to learn individual behaviour

## Population model of variation of $\psi $ across individuals

We assume that the parameters $\psi $ have a structured distribution in the population

\begin{equation*}
    \psi _i \sim \mathbb{P}(\cdot | \theta _{\psi}).
\end{equation*}

For example, we assume that the initial volume of the tumour is log-normally distributed

\begin{equation*}
    \log V_0 \sim \mathcal{N} (\log \mu _{V_0}, \sigma ^2_{V_0})
\end{equation*}

## Advantages of population (hierarchical) approach

1. Inference of individual $\psi $ inform each other
2. Allows exploration of dose-response behaviour of individuals in the population, even if not seen before
3. Can be leveraged to learn personalised doses more robustly and quicker

## Let's see population PKPD approach in action

The distribution of the compound in the mouse system after an oral dose:

\begin{equation*}
\frac{\text{d}A_d}{\text{d}t} = r_d(t) - k_{a}A_d,\qquad \frac{\text{d}A_c}{\text{d}t} = k_{a} A_d - k_e A_c,\qquad C_c = \frac{A_c}{V_c}.
\end{equation*}

Here, $A_d$ is the amount of the compound in the dose compartment, which may be interpreted as the gut compartment, while $A_c$ is the amount in the central compartment which represents the drug in the blood plasma. 

Tumour growth in presence of compound:

\begin{equation*}
\frac{\text{d}V^s_T}{\text{d}t} = \frac{2\lambda _0\lambda _1 V^s_T}{2\lambda _0 V^s_T + \lambda _1} - \kappa C_cV^s_T.
\end{equation*}

Here, $V^s_T$ is the predicted tumour volume by the structural model, $\lambda _0$ is the exponential growth rate, $\lambda _1$ is the linear growth rate, and $\kappa $ is the growth inhibiting potency of the compound.

The dose and central compartment were assumed to initially contain no amount of the compound, $A_d(t=0)=0$ and $A_c(t=0)=0$. The structural model is then parameterised by seven parameters that determine the PKPD of the drug

\begin{equation*}
\psi = (V_0, k_a, k_e, V_c, \lambda _0, \lambda _1, \kappa ),
\end{equation*}

## Population model for variation of $\psi $ in population

All $\psi $ except the absorption rate $k_a$ are assumed to be log-normally distributed in the mouse population

\begin{equation*}
    \log \psi _i \sim \mathcal{N} (\log \mu _i, \sigma ^2_i), \quad \psi _i \neq k_a,
\end{equation*}

where $\mu _i $ is the median of $\psi _i$ in the population, and $\sigma _i$ is the standard deviation of $\log \psi _i$ in the population.

In [4]:
#
# Estimates from Eigenmann et. al. [1] for the Erlotinib and Gefitinib PKPD in LXF A677 and VXF A431.
#

import pandas as pd


# Set display of floats in pandas dataframes to 3 decimals
pd.options.display.float_format = '{:,.3f}'.format

# Create pandas dataframe for LXF A677 Erlotinib model parameters
lxf_erlotinib_estimates = pd.DataFrame(
    data={
        'mu V_0 in cm^3': [0.122, 0.122 * 0.05],
        'sigma V_0 in dimless': [0.368, 0.122 * 0.05],
        'k_a in 1/day': [55.0, None],
        'mu V_c in L': [0.127, 0.127 * 0.15],
        'sigma V_c in dimless': [0.251, None],
        'mu k_e in 1/day': [7.56, 7.56 * 0.1],
        'sigma k_e in dimless': [0.332, 0.332 * 0.39],
        'mu lambda_0 in 1/day': [0.0971, 0.0971 * 0.08],
        'sigma lambda_0 in dimless': [0.456, 0.456 * 0.13],
        'mu lambda_1 in cm^3/day': [0.127, 0.127 * 0.13],
        'sigma lambda_1 in dimless': [0.710, None],
        'mu kappa in L/mg/day': [0.117, 0.117 * 0.17],
        'sigma kappa in dimless': [0.654, 0.654 * 0.21],
        'sigma base in cm^3': [0.0141, 0.0141 * 0.09],
        'sigma rel in dimless': [0.0907, 0.0907 * 0.06]},
    index=['estimate', 'standard deviation'])

# Show dataframe
print('Table 1: Erlotinib LXF A677')
display(lxf_erlotinib_estimates)

Table 1: Erlotinib LXF A677


mu V_0 in cm^3  sigma V_0 in dimless  k_a in 1/day  \
estimate                     0.122                 0.368        55.000   
standard deviation           0.006                 0.006           nan   

                    mu V_c in L  sigma V_c in dimless  mu k_e in 1/day  \
estimate                  0.127                 0.251            7.560   
standard deviation        0.019                   nan            0.756   

                    sigma k_e in dimless  mu lambda_0 in 1/day  \
estimate                           0.332                 0.097   
standard deviation                 0.129                 0.008   

                    sigma lambda_0 in dimless  mu lambda_1 in cm^3/day  \
estimate                                0.456                    0.127   
standard deviation                      0.059                    0.017   

                    sigma lambda_1 in dimless  mu kappa in L/mg/day  \
estimate                                0.710                 0.117   
standard deviation                        nan                 0.020   

                    sigma kappa in dimless  sigma base in cm^3  \
estimate                             0.654               0.014   
standard deviation                   0.137               0.001   

                    sigma rel in dimless  
estimate                           0.091  
standard deviation                 0.005

In [5]:
#
# Sampling mice from the Erlotinib LXF A677, Erlotinib VXF A431, Gefitinib LXF A677 and Gefitinib VXF A431 population.
#
# This cell needs the above defined parameter estimates 
# [lxf_erlotinib_estimates, vxf_erlotinib_estimates, lxf_gefitinib_estimates, vxf_gefitinib_estimates]
#

import numpy as np
from scipy.stats import lognorm


# Define population size
N = 1000

# Number of parameters that define mouse (noise params are not mouse specific)
n_params = 7  # [V_0, k_a, V_c, k_e, lambda_0, lambda_1, kappa]

# Define population parameters
populations = [
    lxf_erlotinib_estimates]
n_populations = len(populations)

# Create container for mice (n_populations, N, n_parameters)
mice_parameters = np.empty(shape=(n_populations, N, n_params))

# Sample mice for each of the populations
for pop_id, population in enumerate(populations):
    # Seed random number generator
    # (Effectively creates the same `virtual` mice in all populations, 
    # i.e. lxf mice 13 will have the same drug-independent growth 
    # parameters wether treated with Erlotinib or Gefitinib)
    np.random.seed(42)

    # Sample initial tumour volumes
    median = population.loc['estimate', 'mu V_0 in cm^3']
    std = population.loc['estimate', 'sigma V_0 in dimless']
    mice_parameters[pop_id, :, 0] = lognorm.rvs(scale=median, s=std, size=N)

    # Sample absorption rate
    mice_parameters[pop_id, :, 1] = np.full(shape=N,fill_value=population.loc['estimate', 'k_a in 1/day'])

    # Sample volume of distribution
    median = population.loc['estimate', 'mu V_c in L']
    std = population.loc['estimate', 'sigma V_c in dimless']
    mice_parameters[pop_id, :, 2] = lognorm.rvs(scale=median, s=std, size=N)

    # Sample elimination rate
    median = population.loc['estimate', 'mu k_e in 1/day']
    std = population.loc['estimate', 'sigma k_e in dimless']
    mice_parameters[pop_id, :, 3] = lognorm.rvs(scale=median, s=std, size=N)

    # Sample exponential growth rate
    median = population.loc['estimate', 'mu lambda_0 in 1/day']
    std = population.loc['estimate', 'sigma lambda_0 in dimless']
    mice_parameters[pop_id, :, 4] = lognorm.rvs(scale=median, s=std, size=N)

    # Sample linear growth rate
    median = population.loc['estimate', 'mu lambda_1 in cm^3/day']
    std = population.loc['estimate', 'sigma lambda_1 in dimless']
    mice_parameters[pop_id, :, 5] = lognorm.rvs(scale=median, s=std, size=N)

    # Sample potency
    median = population.loc['estimate', 'mu kappa in L/mg/day']
    std = population.loc['estimate', 'sigma kappa in dimless']
    mice_parameters[pop_id, :, 6] = lognorm.rvs(scale=median, s=std, size=N)


In [6]:
#
# Simulate tumour growth curves for simulated mice under different dosing strategies.
#
# Dosing strategies: 
# Daily oral administration from day 3 to (including) 16 of
#   0. No treatment
#   1. 25 mg/kg/day (amount drug per mouse weight per day)
#   2. 50 mg/kg/day
#   3. 100 mg/kg/day
# Following [1], all mice in the population are assumed to weigh 20 mg.
#
# This cell needs the above simulated mice parameters and the reference population parameters: 
# [mice_parameeters, populations]
# 

import myokit
from scipy.stats import norm

import pkpd.model as m

# Get population size and number of populations
n_populations = mice_parameters.shape[0]
N = mice_parameters.shape[1]

# Define dosing regimens
# Amount [mg], dose duration [day], start [day], period [day], multiplier [dimless]
mouse_mass = 0.02  # 20 mg
dosing_regimens = [
    [0, 1E-03, 3, 1, 28],  # No treatment
    [6.25 * mouse_mass, 1E-03, 3, 1, 28],
    [25 * mouse_mass, 1E-03, 3, 1, 28],
    [100 * mouse_mass, 1E-03, 3, 1, 28]]
n_regimens = len(dosing_regimens)

# Define percentiles for population summary
percentiles = [10, 25, 50, 75, 90]
n_percentiles = len(percentiles)

# Define simulation time points in days
# Note: concentration needs to be sampled densely to avoid uneven peaks
# due to sampling procedure
times = np.linspace(0, 30, num=900)
n_times = len(times)

# Create container for simulation results 
# Concentration in central compartment + tumour volume
# (n_populations, n_regimens, n_percentiles, 2, n_times)
population_results = np.empty(shape=(
    n_populations, n_regimens, n_percentiles, 2, n_times))

# Create structural model and set route of administration
model = m.create_pktgi_model()
model.set_roa(dose_comp='central', indirect=True)

# Create temporary container for structural model predictions of mice in a population
# (population size, 2, n_times), concentration and tumour volume
mice_dose_response = np.empty(shape=(N, 2, n_times)) 

# Simulate dose-response in population for dosing regimens
for regimen_id, dosing_regimen in enumerate(dosing_regimens):
    # Get regimen
    amount, duration, start, period, multiplier = dosing_regimen

    # Create myokit dosing regimen
    model.set_regimen(
        amount=amount, duration=duration, start=start, period=period, multiplier=multiplier)
    _, protocol = model.dosing_regimen()

    # Create simulator
    simulator = myokit.Simulation(model, protocol)

    # Loop through populations
    # Recall: mice_parameters shape = (n_populations, N, n_parameters)
    for pop_id, population in enumerate(mice_parameters):
        
        # Loop through indiviuals in population
        # 'mouse' contains parameters: [V_0, k_a, V_c, k_e, lambda_0, lambda_1, kappa]
        for mouse_id, mouse in enumerate(population):
            # Reset simulator
            simulator.reset()

            # Set initial state
            # central.amount, central.volume_t, depot.amount
            simulator.set_state([0, mouse[0], 0])

            # Set parameters
            simulator.set_constant('depot.k_a', mouse[1])
            simulator.set_constant('central.volume_c', mouse[2])
            simulator.set_constant('central.k_e', mouse[3])
            simulator.set_constant('central.lambda_0', mouse[4])
            simulator.set_constant('central.lambda_1', mouse[5])
            simulator.set_constant('central.kappa', mouse[6])

            # Define logged variable
            logged_variables = ['central.conc', 'central.volume_t']

            # Solve structural model
            output = simulator.run(times[-1] + 1, log=logged_variables, log_times=times)

            # Convert myokit.DataLog into numpy array
            for var_id, var in enumerate(logged_variables):
                mice_dose_response[mouse_id, var_id, :] = np.array(output[var])

        # Add error model predictions to structural model predictions
        # Get sigma base and sigma rel from dataframe
        sigma_base = populations[pop_id].loc['estimate', 'sigma base in cm^3']
        sigma_rel = populations[pop_id].loc['estimate', 'sigma rel in dimless']

        # Draw standard Gaussian random variable for each predicted tumour volume
        gaussian_rv = np.random.normal(loc=0.0, scale=1.0, size=mice_dose_response[:, 1, :].shape)

        # Scale random variable according to error model
        # Eps = (sigma_base + sigma_rel * V^s_T) * gaussian_rv
        gaussian_rv *= sigma_base #(sigma_base + sigma_rel * mice_dose_response)

        # Overlay error model predictions on structural model predictions
        mice_dose_response[:, 1, :] += gaussian_rv

        # Compute population percentiles
        for perc_id, percentile in enumerate(percentiles):
            population_results[pop_id, regimen_id, perc_id, ...] = np.percentile(
                a=mice_dose_response, q=percentile, axis=0)


In [7]:
#
# Convert dosing regimen into time series for illustration.
#

# Create container for dosing regimen time series
dosing_time_series = []

# Compute dosing regimen time series
for regimen in dosing_regimens:
    amount, duration, start, period, multiplier = regimen

    # Initialise container (start with zero amount at time 0, and continue to end of simulation)
    # Construct series by adding a point at dosing start and after finishing the dose.
    dose_series = np.zeros(shape=(2, 2*multiplier+2))

    # Construct dosing times
    dose_series[0, 1:-2:2] = np.arange(
        start=start, 
        stop=start+period*multiplier,
        step=period)  # time points of dose start
    dose_series[0, 2:-1:2] = dose_series[0, 1:-2:2] + duration  # time points of dose end
    
    # Compute dose amount administered
    dose_series[1, 1:-2:2] = np.arange(multiplier) * amount  # Start of dose
    dose_series[1, 2:-1:2] = np.arange(1, multiplier+1) * amount

    # Repeat last full amount for the rest of the simulation period
    dose_series[0, -1] = times[-1]
    dose_series[1, -1] = dose_series[1, -2]

    # Append to container
    dosing_time_series.append(dose_series)

In [20]:
#
# Illustrate population PKPD simulation.
#
# Needs above defined dosing regimens, percentiles, times, simulation results,
# and the population size:
# [dosing_regimens, percentiles, times, population_results, N]
#

import plotly.graph_objects as go
from plotly.subplots import make_subplots


# Create figure
fig = make_subplots(rows=3, cols=1, shared_xaxes=True, row_heights=[0.2, 0.4, 0.4], vertical_spacing=0.05)

# Plot simulations for different dosing strategies
for dose_id, dose_series in enumerate(dosing_time_series):
    # Plot administered drug
    fig.add_trace(
        go.Scatter(
            x=dose_series[0, :],
            y=dose_series[1, :],
            name="Dosed amount",
            hovertemplate=
                    "<b></b>Cumulative amount of compound<br>" +
                    "Time: %{x:.0f} day<br>" +
                    "Amount: %{y:.01f} mg<br>" +
                    "<extra></extra>",
            line=dict(color='rgb(0, 0, 0)'),
            mode='lines',
            opacity=0.3,
            visible = dose_id == 0),  # Only show first dosing regimen
        row=1,
        col=1)

    # Plot data LXF A677 Erlotinib
    # Plot 10th percentile to 90th precentile of the concentration in the central compartment
    fig.add_trace(
        go.Scatter(
            x=np.hstack([times,times[::-1]]),
            # Shape population_results: (n_populations, n_regimens, n_percentiles, 2, n_times) 
            y=np.hstack([
                population_results[0, dose_id, 0, 0, :], 
                population_results[0, dose_id, 4, 0, ::-1]]),
            line=dict(width=1, color='rgb(51, 153, 255)'),
            fill='toself',
            legendgroup="LXF A677 Erlotinib",
            name="10th to 90th percentile",
            hoverinfo='name',
            showlegend=False,
            visible = dose_id == 0),  # Only show first dosing regimen
        row=2,
        col=1)
    
    # Plot 25th percentile to 75th precentile of the concentration in the central compartment
    fig.add_trace(
        go.Scatter(
            x=np.hstack([times,times[::-1]]),
            # Shape population_results: (n_populations, n_regimens, n_percentiles, 2, n_times)
            y=np.hstack([
                population_results[0, dose_id, 1, 0, :], 
                population_results[0, dose_id, 3, 0, ::-1]]),
            line=dict(width=1, color='rgb(0, 128, 255)'),
            fill='toself',
            legendgroup="LXF A677 Erlotinib",
            name="25th to 75th percentile",
            hoverinfo='name',
            showlegend=False,
            visible = dose_id == 0),  # Only show first dosing regimen
        row=2,
        col=1)
    
    # Plot Median of the concentration in the central compartment
    fig.add_trace(
        go.Scatter(
            x=times,
            # Shape population_results: (n_populations, n_regimens, n_percentiles, 2, n_times)
            y=population_results[0, dose_id, 2, 0, :],
            legendgroup="LXF A677 Erlotinib",
            name="LXF A677 Erlotinib",
            hovertemplate=
                    "<b></b>Median<br>" +
                    "Population size: %d<br>" % N +
                    "Time: %{x:.02f} day<br>" +
                    "Concentration in central compartment: %{y:.02f} mg/L<br>" +
                    "<extra></extra>",
            line=dict(color='rgb(0, 102, 204)'),
            visible = dose_id == 0),  # Only show first dosing regimen
        row=2,
        col=1)
    
    # Plot 10th percentile to 90th precentile of the tumour volume
    fig.add_trace(
        go.Scatter(
            x=np.hstack([times,times[::-1]]),
            # Shape population_results: (n_populations, n_regimens, n_percentiles, 2, n_times)
            y=np.hstack([
                population_results[0, dose_id, 0, 1, :], 
                population_results[0, dose_id, 4, 1, ::-1]]),
            line=dict(width=1, color='rgb(51, 153, 255)'),
            fill='toself',
            legendgroup="LXF A677 Erlotinib",
            name="10th to 90th percentile",
            hoverinfo='name',
            showlegend=False,
            visible = dose_id == 0),  # Only show first dosing regimen
        row=3,
        col=1)

    # Plot 25th percentile to 75th precentile of the tumour volume
    fig.add_trace(
        go.Scatter(
            x=np.hstack([times,times[::-1]]),
            # Shape population_results: (n_populations, n_regimens, n_percentiles, 2, n_times)
            y=np.hstack([
                population_results[0, dose_id, 1, 1, :], 
                population_results[0, dose_id, 3, 1, ::-1]]),
            line=dict(width=1, color='rgb(0, 128, 255)'),
            fill='toself',
            legendgroup="LXF A677 Erlotinib",
            name="25th to 75th percentile",
            hoverinfo='name',
            showlegend=False,
            visible = dose_id == 0),  # Only show first dosing regimen
        row=3,
        col=1)

    # Plot Median of the tumour volume
    fig.add_trace(
        go.Scatter(
            x=times,
            # Shape population_results: (n_populations, n_regimens, n_percentiles, 2, n_times)
            y=population_results[0, dose_id, 2, 1, :],
            legendgroup="LXF A677 Erlotinib",
            name="LXF A677 Erlotinib",
            hovertemplate=
                    "<b></b>Median<br>" +
                    "Population size: %d<br>" % N +
                    "Time: %{x:.02f} day<br>" +
                    "Tumour volume: %{y:.02f} cm^3<br>" +
                    "<extra></extra>",
            line=dict(color='rgb(0, 102, 204)'),
            showlegend=False,
            visible = dose_id == 0),  # Only show first dosing regimen
        row=3,
        col=1)

# Set figure size
fig.update_layout(
    autosize=True,
    template="plotly_white",
    margin=dict(
        l=0,
        r=0))

# Set X axis label
fig.update_xaxes(title_text=r'$\text{Time in day}$', row=3, col=1)

# Set Y axes labels
fig.update_yaxes(title_text=r'$\text{Amount in mg}$', row=1, col=1)
fig.update_yaxes(title_text=r'$\text{Conc. in mg/L}$', row=2, col=1)
fig.update_yaxes(title_text=r'$\text{Tumour volume in cm}^3$', row=3, col=1)

# Add switch between linear and log y-scale, and switches between dosing regimens
fig.update_layout(
    updatemenus=[
        dict(
            type = "buttons",
            direction = "right",
            buttons=list([
                dict(
                    args=[{"visible": [True]*7 + [False]*7 + [False]*7 + [False]*7}],
                    label="No treatment",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*7 + [True]*7 + [False]*7 + [False]*7}],
                    label="6.25 mg/kg/day",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*7 + [False]*7 + [True]*7 + [False]*7}],
                    label="25 mg/kg/day",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*7 + [False]*7 + [False]*7 + [True]*7}],
                    label="100 mg/kg/day",
                    method="restyle"
                )
            ]),
            pad={"r": 0, "t": -10},
            showactive=True,
            x=0.0,
            xanchor="left",
            y=1.1,
            yanchor="top"
        ),
    ]
)

# Position legend
fig.update_layout(legend=dict(
    yanchor="top",
    y=0.4,
    xanchor="left",
    x=0.01))

# Show figure
fig.show()


In [21]:
fig.write_html(file="simulation.html", full_html=False, include_plotlyjs=False, include_mathjax='cdn')

In [15]:
#
# Illustrate convergence of indiviually fitted parameters with population model.
#
# This cell needs above defined wrapped myokit model:
# [PintsModel]
#

import os

import numpy as np
import pandas as pd
import pints

import pkpd.model as m


# Import data
# Get path of directory one up current working directory
path = os.path.dirname(os.getcwd())

# Import LXF A677 control growth data
lxf_data = pd.read_csv(path + '/notebooks/control_growth/data/lxf_control_growth.csv')

# Get a mouse 
mice_ids = lxf_data['#ID'].unique()
mask = lxf_data['#ID'] == mice_ids[0]
mouse_data = lxf_data[mask]

# Get relevant time points
all_times = mouse_data['TIME in day'].to_numpy()
n_times = len(all_times)

# Get measured tumour volumes
all_observed_volumes = mouse_data['TUMOUR VOLUME in cm^3'].to_numpy()

# Define container for the structural model estimates when
# for each inference data is used up to a specfied time point
# Shape (n_data_points, n_parameters)
n_parameters = 5
mouse_parameters = np.empty(shape=(n_times, n_parameters))

# Define arbitrary starting point for the optimisations
initial_parameters = [0.122, 0.097, 0.127, 1, 0.1]

# Find mouse parameters for mice by iteratively appending measurements
for data_id in range(n_times):
    # Get relevant time points
    times = all_times[:data_id+1]

    # Get measured tumour volumes
    observed_volumes = all_observed_volumes[:data_id+1]

    # Create inverse problem
    problem = pints.SingleOutputProblem(PintsModel(), times, observed_volumes)

    # Create likelihood
    likelihood = pints.MultiplicativeGaussianLogLikelihood(problem)

    # Create priors
    prior_v0 = pints.LogNormalLogPrior(
        log_mean=np.log(0.122),
        scale=0.368,
    )
    prior_lambda0 = pints.LogNormalLogPrior(
        log_mean=np.log(0.097),
        scale=0.456,
    )
    prior_lambda1 = pints.LogNormalLogPrior(
        log_mean=np.log(0.127),
        scale=0.710,
    )
    prior_eta = pints.UniformLogPrior(0.9, 1.1)
    prior_sigma = pints.UniformLogPrior(0.001, 1E3)

    # Compose prior
    prior = pints.ComposedLogPrior(
        prior_v0, prior_lambda0, prior_lambda1, prior_eta, prior_sigma)

    # Create posterior
    posterior = pints.LogPosterior(likelihood, prior)

    # Create optimisation controller with a CMA-ES optimiser
    optimiser = pints.OptimisationController(
        function=posterior,
        x0=initial_parameters,
        method=pints.CMAES)

    # Disable logging mode
    optimiser.set_log_to_screen(False)

    # Parallelise optimisation
    optimiser.set_parallel(True)

    # Find optimal parameters
    estimates, _ = optimiser.run()

    # Save estimates
    mouse_parameters[data_id, :] = estimates

/Users/david/Documents/SABS/DPhil/Rotation 1 - PKPD Modelling Workflow/notebooks/ErlotinibGefitinib/venv/lib/python3.7/site-packages/cma/evolution_strategy.py:3591: RuntimeWarning:

invalid value encountered in double_scalars



In [16]:
#
# Solve structural model for inferred model parameters.
#
# This cell needs the above defined wrapped myokit model, and the inferred model parameters:
# [PintsModel, mouse_parameters]
#

import numpy as np


# Create tumour growth model
model = PintsModel()

# Define simulation time points in day
times = np.linspace(start=0, stop=30)
n_times_sim = len(times)

# Create container for simulated tumour growth
# Shape (n_times_data, n_times_sim)
n_times_data = len(mouse_parameters)
simulated_tumour_growth = np.empty(shape=(n_times_data, n_times_sim))

# Solve structural model for LXF A677 population
for params_id, mouse_params in enumerate(mouse_parameters):
    # Get relevant parameters [intial volume, lamda_0, lambda_1]
    params = mouse_params[:3]
    
    # Simulate mouse tumour growth
    simulated_tumour_growth[params_id, :] = model.simulate(parameters=params, times=times)


In [17]:
#
# Visualise simulated tumour growth together with control growth data.
#
# This cell needs the above simulated tumour growth and the control growth data:
# [times, simulated_tumour_growth, mouse_data]
#

import pandas as pd
import plotly.colors
import plotly.graph_objects as go


# Get number of optimisations
n_opt = len(simulated_tumour_growth)

# Define colorscheme
color = plotly.colors.qualitative.Plotly[0]

# Create figure
fig = go.Figure()

# Get Mouse id
mouse_id = mouse_data['#ID'][0]

# Get relevant time points
all_times = mouse_data['TIME in day'].to_numpy()
n_times = len(all_times)

# Get measured tumour volumes
all_observed_volumes = mouse_data['TUMOUR VOLUME in cm^3'].to_numpy()

# Scatter plot mouse data up to specified time
for data_id in range(n_times):
    # Get training data times
    observed_times_train = all_times[:data_id+1]

    # Get remaining data times
    observed_times = all_times[data_id+1:]

    # Get training data volumes
    observed_volumes_train = all_observed_volumes[:data_id+1]

    # remaining data volumes
    observed_volumes = all_observed_volumes[data_id+1:]

    # Get simulated tumour volumes for mouse
    simulated_volumes = simulated_tumour_growth[data_id, :]

    # Plot data train data
    fig.add_trace(go.Scatter(
        x=observed_times_train,
        y=observed_volumes_train,
        legendgroup="ID: %d" % mouse_id,
        name="ID: %d" % mouse_id,
        showlegend=True,
        visible=True if data_id == 0 else False,
        hovertemplate=
            "<b>Measurements %s</b><br>" % ("LXF A677") +
            "ID: %d<br>" % mouse_id +
            "Time: %{x:} day<br>" +
            "Tumour volume: %{y:.02f} cm^3<br>" +
            "<extra></extra>",
        mode="markers",
        marker=dict(
            symbol='circle',
            opacity=0.7,
            line=dict(color='black', width=1),
            color=color)
    ))

    # Plot data remaining data
    fig.add_trace(go.Scatter(
        x=observed_times,
        y=observed_volumes,
        legendgroup="ID: %d" % mouse_id,
        name="ID: %d" % mouse_id,
        showlegend=False,
        visible=True if data_id == 0 else False,
        hovertemplate=
            "<b>Measurements %s</b><br>" % ("LXF A677") +
            "ID: %d<br>" % mouse_id +
            "Time: %{x:} day<br>" +
            "Tumour volume: %{y:.02f} cm^3<br>" +
            "<extra></extra>",
        mode="markers",
        marker=dict(
            symbol='circle',
            opacity=0.2,
            line=dict(color='black', width=1),
            color=color)
    ))

    # Plot simulated growth
    fig.add_trace(go.Scatter(
        x=times,
        y=simulated_volumes,
        legendgroup="ID: %d" % mouse_id,
        name="ID: %d" % mouse_id,
        showlegend=False,
        visible=True if data_id == 0 else False,
        hovertemplate=
            "<b>Simulation %s</b><br>" % ("LXF A677") +
            "ID: %d<br>" % mouse_id +
            "Time: %{x:.0f} day<br>" +
            "Tumour volume: %{y:.02f} cm^3<br>" +
            "<extra></extra>",
        mode="lines",
        line=dict(color=color)
    ))

# Set figure size
fig.update_layout(
    autosize=False,
    width=800,
    height=600,
    template="plotly_white")


# Set X axis label
fig.update_xaxes(title_text=r'$\text{Time in day}$')

# Set Y axes labels
fig.update_yaxes(title_text=r'$\text{Tumour volume in cm}^3$')

# Add switch between linear and log y-scale
fig.update_layout(
    updatemenus=[
        dict(
            type = "buttons",
            direction = "left",
            buttons=list([
                dict(
                    args=[{"yaxis.type": "linear"}],
                    label="Linear y-scale",
                    method="relayout"
                ),
                dict(
                    args=[{"yaxis.type": "log"}],
                    label="Log y-scale",
                    method="relayout"
                )
            ]),
            pad={"r": 0, "t": -10},
            showactive=True,
            x=0.0,
            xanchor="left",
            y=1.15,
            yanchor="top"
        ),
        dict(
            type = "buttons",
            direction = "down",
            buttons=list([
                dict(
                    args=[{"visible": [True]*3 + [False]*(3 * (n_times - 1))}],
                    label="1 data point",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*3 + [True]*3 + [False]*(3 * (n_times - 2))}],
                    label="2 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 2) + [True]*3 + [False]*(3 * (n_times - 3))}],
                    label="3 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 3) + [True]*3 + [False]*(3 * (n_times - 4))}],
                    label="4 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 4) + [True]*3 + [False]*(3 * (n_times - 5))}],
                    label="5 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 5) + [True]*3 + [False]*(3 * (n_times - 6))}],
                    label="6 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 6) + [True]*3 + [False]*(3 * (n_times - 7))}],
                    label="7 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 7) + [True]*3 + [False]*(3 * (n_times - 8))}],
                    label="8 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 8) + [True]*3 + [False]*(3 * (n_times - 9))}],
                    label="9 data points",
                    method="restyle"
                ),
                dict(
                    args=[{"visible": [False]*(3 * 9) + [True]*3 + [False]*(3 * (n_times - 10))}],
                    label="10 data points",
                    method="restyle"
                )
            ]),
            pad={"r": 0, "t": -10},
            showactive=True,
            x=1.07,
            xanchor="left",
            y=1.1,
            yanchor="top"
        ),
    ]
)

# Position legend
fig.update_layout(legend=dict(
    yanchor="bottom",
    y=0.01,
    xanchor="left",
    x=1.05))

# Show figure
fig.show()

## Take home

1. A standard dose for everybody is not enough
2. Population PKPD modelling is a way to go about it

## Acknowledgments

Big thanks to 

Antje, Ken, Dave, George, Simon and Rebecca